In [1]:
import pandas as pd 
import numpy as np

In [2]:
data = pd.read_parquet('jane-street-real-time-market-data-forecasting/train.parquet/partition_id=3/part-0.parquet')

In [3]:
for symbol in data['symbol_id'].unique():
    if data.loc[data['symbol_id']==symbol].feature_09.unique().shape[0] != 1:
        print(f"{symbol}- feature_09")
    if data.loc[data['symbol_id']==symbol].feature_10.unique().shape[0] != 1:
        print(f"{symbol}- feature_10")
    if data.loc[data['symbol_id']==symbol].feature_11.unique().shape[0] != 1:
        print(f"{symbol}- feature_11")

20- feature_09
20- feature_10
20- feature_11
26- feature_11
36- feature_09
36- feature_10
36- feature_11


In [4]:
data.loc[data['symbol_id']==20].feature_09.unique()

array([42, 30], dtype=int8)

In [5]:
print(f"feature_09: {data.feature_09.unique()}, shape: {data.feature_09.unique().shape}")
print(f"feature_10: {data.feature_10.unique()}, shape: {data.feature_10.unique().shape}")
print(f"feature_11: {data.feature_11.unique()}, shape: {data.feature_11.unique().shape}")

feature_09: [11 81  4  2 15 42 46 70 50 44  9 64 34 30 57 26 68], shape: (17,)
feature_10: [ 7  2  3 10  1  5  6  4 12], shape: (9,)
feature_11: [ 76  59  11 171  62 150 261 410 522  16  25 376 214  13 230 159 336 534
 158 388  50], shape: (21,)


In [6]:
17 * 9 * 21

3213

In [14]:
# 실제 unique 조합 확인
unique_combinations = data[['feature_09', 'feature_10', 'feature_11']].drop_duplicates()

# 조합 수와 실제 조합들 출력
print(f"실제 unique 조합의 수: {len(unique_combinations)}")

# 각 조합의 출현 빈도도 확인
combination_counts = data.groupby(['feature_09', 'feature_10', 'feature_11']).size().reset_index(name='count')
combination_counts = combination_counts.sort_values('count', ascending=False)
print("\n전체 unique 조합:")
combination_counts.reset_index(drop=True)

실제 unique 조합의 수: 21

전체 unique 조합:


feature_09  feature_10  feature_11   count
0           11           7          76  829917
1           42           5         150  336069
2            4           3          11  287676
3           34           4         214  243528
4           50           1         522  243528
5           26          12         158  155724
6           81           2         534  144687
7            2          10         171  144687
8           70           7         410  144687
9           44           3          16  144687
10          81           2          59  144687
11          57           1         336  144687
12          30          10          13  144687
13          46           3         261  143838
14           9           3          25  143838
15          57           1         230  143838
16          64           6         376  142989
17          68           6         388  122613
18          15           1          62  103935
19          30          10          50   97143
20          26          12         159    9339

In [16]:
def create_group_mapper(group_df):
    """
    그룹 매핑을 위한 dictionary 생성
    """
    return {
        (row['feature_09'], row['feature_10'], row['feature_11']): idx 
        for idx, row in group_df.iterrows()
    }

def map_to_group_vectorized(data, group_mapper):
    """
    벡터 연산을 사용하여 데이터를 그룹에 매핑
    """
    # 매핑을 위한 복합 키 생성
    combined_key = pd.Series(list(zip(data['feature_09'], 
                                    data['feature_10'], 
                                    data['feature_11'])))
    
    # numpy의 vectorize 사용하여 매핑
    vectorized_mapper = np.vectorize(lambda x: group_mapper.get(x, -1))
    
    return vectorized_mapper(combined_key)

In [17]:
group_info = combination_counts.reset_index(drop=True).drop('count', axis=1)

# 그룹 매퍼 생성
group_mapper = create_group_mapper(group_info)

# 그룹 매핑 실행
data['group'] = map_to_group_vectorized(data, group_mapper)

한 partition이긴 하지만 실제 조합은 21개 밖에 없는 것을 볼 수 있음. 

- 하지만 이 조합이 symbol을 대표할 수 있는지를 알아야함.
- corr을 해보기에는 데이터가 너무 많아서 잘 안됨. 그리고 어떤 feature에 대해서 corr을 적용할지도 애매함. 

1. 시각화 진행 
    - 모든 timestamp에 대해서 시각화하는건 보기도 어렵고 쉽지 않음. 따라서 time_id로 groupby해서 진행할 예정
        - 이전에도 time_id에서 symbol마다 다른 시계열성이 존재함을 관찰할 수 있었기 때문에 이 분석은 타당하다고 생각함. 
     
2. 통계 분석
    - 조합에 따른 feature를 분석해볼 수 있을 것 같다. 
    - 각 조합으로 데이터를 묶은뒤에 feature별로 분산분석!

## 시각화

In [26]:
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
from datetime import datetime

def visualize_group_features(data, feature_cols, n_groups=21):
    # Set figure size
    plt.figure(figsize=(30, 200))

    print(f"[{datetime.now().strftime('%H:%M:%S')}] 시각화 시작...")

    # Create time series for each group and feature
    print(f"[{datetime.now().strftime('%H:%M:%S')}] 그룹별 시계열 데이터 생성 중...")
    
    # Calculate grid dimensions
    n_features = len(feature_cols)
    
    print(f"[{datetime.now().strftime('%H:%M:%S')}] 그래프 그리기 시작...")
    
    # Create subplots
    for feature_idx, feature in enumerate(feature_cols):
        if (feature_idx + 1) % 10 == 0:
            print(f"[{datetime.now().strftime('%H:%M:%S')}] Feature 처리 중... ({feature_idx+1}/{n_features})")
        
        for group in range(n_groups):
            # Filter data for current group
            group_data = data[data['group'] == group]
            
            # Calculate time-based means for the current group and feature
            time_means = group_data.groupby('time_id')[feature].mean()
            
            # Calculate subplot position (features as rows, groups as columns)
            plt.subplot(n_features, n_groups, feature_idx * n_groups + group + 1)
            
            # Plot the data
            plt.plot(time_means.index, time_means.values)
            
            # Add titles and labels
            if group == 0:  # Only add feature name on the leftmost plot
                plt.ylabel(feature, rotation=0, ha='right')
            if feature_idx == 0:  # Only add group number on the top row
                plt.title(f'Group {group}')
            
            # Remove x-axis labels to save space
            plt.xticks([])
            
            # Remove y-axis labels for all but leftmost plots
            if group != 0:
                plt.yticks([])

    print(f"[{datetime.now().strftime('%H:%M:%S')}] 레이아웃 조정 중...")
    plt.tight_layout()

    print(f"[{datetime.now().strftime('%H:%M:%S')}] 그래프 표시 중...")
    plt.show()

    print(f"[{datetime.now().strftime('%H:%M:%S')}] 작업 완료!")

In [27]:
# feature 컬럼 리스트 생성
feature_cols = [col for col in data.columns if 'feature' in col] + [
    'responder_1', 'responder_2', 'responder_3', 
    'responder_4', 'responder_5', 'responder_6'
]

# 시각화 실행
visualize_group_features(data, feature_cols)

[17:02:53] 시각화 시작...
[17:02:53] 그룹별 시계열 데이터 생성 중...
[17:02:53] 그래프 그리기 시작...
[17:03:06] Feature 처리 중... (10/85)
[17:03:22] Feature 처리 중... (20/85)
[17:03:37] Feature 처리 중... (30/85)
[17:03:53] Feature 처리 중... (40/85)
[17:04:08] Feature 처리 중... (50/85)
[17:04:25] Feature 처리 중... (60/85)
[17:04:41] Feature 처리 중... (70/85)
[17:04:57] Feature 처리 중... (80/85)
[17:05:08] 레이아웃 조정 중...
[17:05:12] 그래프 표시 중...


[17:05:22] 작업 완료!


## ANOVA 통계분석

In [25]:
import pandas as pd
import numpy as np
from scipy import stats
from typing import List, Dict

def analyze_feature_groups_with_anova(
    data: pd.DataFrame,
    features: List[str],
    group_column: str
) -> pd.DataFrame:
    """
    각 feature별로 군집 간 통계량과 ANOVA 분석 결과를 비교하는 함수
    
    Parameters:
    -----------
    data : DataFrame
        분석할 원본 데이터
    features : List[str]
        분석할 feature 컬럼들의 리스트
    group_column : str
        군집을 나타내는 컬럼명
    """
    results = []
    
    # 전체 데이터의 통계량
    total_stats = data[features].agg(['mean', 'std']).round(4)
    
    # 각 feature별로 분석
    for feature in features:
        # 전체 데이터 통계량
        total_mean = total_stats.loc['mean', feature]
        total_std = total_stats.loc['std', feature]
        
        # 군집별 통계량
        group_stats = data.groupby(group_column)[feature].agg(['mean', 'std']).round(4)
        
        # 군집 내 표준편차의 평균
        mean_group_std = group_stats['std'].mean()
        
        # 군집 간 평균의 표준편차
        between_group_std = group_stats['mean'].std()
        
        # ANOVA 분석
        groups = [group[feature].values for name, group in data.groupby(group_column)]
        f_stat, p_value = stats.f_oneway(*groups)
        
        # 에타 제곱(효과 크기) 계산
        df_between = len(groups) - 1
        df_within = len(data) - len(groups)
        eta_squared = (f_stat * df_between) / (f_stat * df_between + df_within)
        
        results.append({
            'feature': feature,
            'total_mean': total_mean,
            'total_std': total_std,
            'mean_within_group_std': mean_group_std,
            'between_group_std': between_group_std,
            'std_reduction_pct': ((total_std - mean_group_std) / total_std * 100).round(2),
            'group_separation': (between_group_std / mean_group_std).round(2),
            'f_statistic': round(f_stat,4),
            'p_value': p_value,
            'eta_squared': round(eta_squared, 4)
        })
    
    # 결과를 DataFrame으로 변환
    results_df = pd.DataFrame(results)
    
    # 유의성 표시 추가
    results_df['significance'] = results_df['p_value'].apply(
        lambda x: '***' if x < 0.001 else
                 ('**' if x < 0.01 else
                 ('*' if x < 0.05 else 'ns'))
    )
    
    # 효과 크기 해석 추가
    results_df['effect_size'] = results_df['eta_squared'].apply(
        lambda x: 'Large' if x >= 0.14 else
                 ('Medium' if x >= 0.06 else
                 ('Small' if x >= 0.01 else 'Negligible'))
    )
    
    # eta_squared를 기준으로 정렬
    results_df = results_df.sort_values('eta_squared', ascending=False)
    
    return results_df

def print_analysis_summary(results_df: pd.DataFrame, top_n: int = 10):
    """
    분석 결과 요약 출력
    """
    print(f"\n=== 군집 효과가 가장 큰 상위 {top_n}개 Feature ===")
    summary = results_df.head(top_n)[['feature', 'std_reduction_pct', 'f_statistic', 
                                    'p_value', 'eta_squared', 'significance', 'effect_size']]
    
    print(summary.to_string(index=False))
    
    print("\n=== 통계적 유의성 분포 ===")
    sig_counts = results_df['significance'].value_counts()
    print(sig_counts)
    
    print("\n=== 효과 크기 분포 ===")
    effect_counts = results_df['effect_size'].value_counts()
    print(effect_counts)

In [ ]:
results = analyze_feature_groups_with_anova(
    data=data.fillna(data.mean()),
    features=data.columns,  # 78개 feature 리스트
    group_column='group'  # 21개 군집을 나타내는 컬럼
)

In [24]:
# 상위 10개 feature에 대한 요약 출력
print_analysis_summary(results, top_n=100)


=== 군집 효과가 가장 큰 상위 100개 Feature ===
    feature  std_reduction_pct  f_statistic      p_value  eta_squared significance effect_size
 feature_30          68.750000 8.224888e+05 0.000000e+00       0.8037          ***       Large
 feature_29          69.849998 6.823477e+05 0.000000e+00       0.7726          ***       Large
 feature_23          62.279999 5.345033e+05 0.000000e+00       0.7269          ***       Large
 feature_20          50.160000 4.429493e+05 0.000000e+00       0.6880          ***       Large
 feature_17          49.689999 3.629161e+05 0.000000e+00       0.6437          ***       Large
 feature_15          49.910000 3.181531e+05 0.000000e+00       0.6130          ***       Large
 feature_22          58.360001 3.102110e+05 0.000000e+00       0.6070          ***       Large
  symbol_id          78.930000 2.489870e+05 0.000000e+00       0.5535          ***       Large
     weight          63.779999 2.459309e+05 0.000000e+00       0.5505          ***       Large
 feature_26  